In [1]:
import ee
import geemap
import folium
from folium import plugins
from folium.plugins import FloatImage
import os

In [2]:
ee.Authenticate()
ee.Initialize(project='gee-map-id')

In [5]:

# Load Sri Lanka boundary and districts
sri_lanka = ee.FeatureCollection("FAO/GAUL/2015/level0") \
    .filter(ee.Filter.eq("ADM0_NAME", "Sri Lanka"))

districts = ee.FeatureCollection("FAO/GAUL/2015/level1") \
    .filter(ee.Filter.eq("ADM0_NAME", "Sri Lanka"))

# Sentinel-2 ImageCollection
image = (
    ee.ImageCollection("COPERNICUS/S2_SR_HARMONIZED")
    .filterBounds(sri_lanka)
    .filterDate("2021-01-01", "2021-12-31")
    .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 10))
    .median()
    .clip(sri_lanka)
    .select(["B2", "B3", "B4", "B8"])
)

# Training samples (Vegetation, Flat Lands, Urban)
vegetation = ee.FeatureCollection([
    ee.Feature(ee.Geometry.Point([80.7698, 7.8731]), {"landcover": 0}),
    ee.Feature(ee.Geometry.Point([80.7748, 7.8781]), {"landcover": 0}),
])

flatlands = ee.FeatureCollection([
    ee.Feature(ee.Geometry.Point([80.7715, 7.8700]), {"landcover": 1}),
    ee.Feature(ee.Geometry.Point([80.7750, 7.8650]), {"landcover": 1}),
])

urban = ee.FeatureCollection([
    ee.Feature(ee.Geometry.Point([80.7800, 7.8800]), {"landcover": 2}),
    ee.Feature(ee.Geometry.Point([80.7840, 7.8830]), {"landcover": 2}),
])

training_points = vegetation.merge(flatlands).merge(urban)

# Classify
bands = ["B2", "B3", "B4", "B8"]
label = "landcover"
training = image.select(bands).sampleRegions(
    collection=training_points,
    properties=[label],
    scale=10
)

classifier = ee.Classifier.smileRandomForest(50).train(
    features=training, classProperty=label, inputProperties=bands
)

classified = image.select(bands).classify(classifier)

# Create folium map
folium_map = folium.Map(location=[7.8731, 80.7718], zoom_start=7)

# Add Sentinel-2 background (optional)
rgb_vis = {
    "min": 0,
    "max": 3000,
    "bands": ["B8", "B4", "B3"],
}
image_rgb = image.visualize(**rgb_vis)
image_mapid = image_rgb.getMapId()
folium.TileLayer(
    tiles=image_mapid['tile_fetcher'].url_format,
    attr="Sentinel-2 RGB",
    name="Sentinel-2 RGB",
    overlay=True,
    control=True
).add_to(folium_map)

# Add classified map
classified_vis = {
    "min": 0,
    "max": 2,
    "palette": ["006400", "FFD700", "808080"],  # Vegetation, Flatlands, Urban
}
classified_mapid = classified.getMapId(classified_vis)
folium.TileLayer(
    tiles=classified_mapid['tile_fetcher'].url_format,
    attr="Land Cover Classification",
    name="Land Cover",
    overlay=True,
    control=True
).add_to(folium_map)

# Create a legend
legend_html = '''
<div style="position: fixed;
            bottom: 30px; left: 30px; width: 180px; height: 110px;
            background-color: white; border:2px solid black; z-index:9999;
            font-size: 14px; padding: 10px;">
    <strong>Land Cover Legend</strong><br>
    <i style="background: #006400; width: 20px; height: 20px; display: inline-block;"></i> Vegetation<br>
    <i style="background: #FFD700; width: 20px; height: 20px; display: inline-block;"></i> Flat Lands<br>
    <i style="background: #808080; width: 20px; height: 20px; display: inline-block;"></i> Urban<br>
</div>
'''
folium_map.get_root().html.add_child(folium.Element(legend_html))

# Create district dropdown and boundary overlay logic
district_list = districts.aggregate_array("ADM1_NAME").getInfo()

# Add all district polygons to map (hidden by default)
district_layers = {}
for dist_name in district_list:
    feature = districts.filter(ee.Filter.eq("ADM1_NAME", dist_name)).geometry()
    geojson = geemap.ee_to_geojson(feature)
    layer = folium.GeoJson(
        geojson,
        name=dist_name,
        style_function=lambda x: {"fillOpacity": 0, "color": "red", "weight": 2}
    )
    district_layers[dist_name] = layer
    layer.add_to(folium_map)

# Add dropdown to select district
dropdown = '''
<div style="position: fixed; top: 30px; left: 30px; z-index:9999; background: white; padding: 10px; border: 2px solid black;">
    <label for="district">Select District:</label><br>
    <select id="district" onchange="selectDistrict(this.value)">
        <option value="">--Choose--</option>
'''
for dist_name in district_list:
    dropdown += f'<option value="{dist_name}">{dist_name}</option>'
dropdown += '''
    </select>
</div>

<script>
function selectDistrict(districtName) {
    var layers = document.getElementsByClassName("leaflet-interactive");
    for (var i = 0; i < layers.length; i++) {
        var layer = layers[i];
        if (layer.getAttribute("stroke") === "red") {
            layer.style.display = "none";
        }
    }
    var mapLayers = document.getElementsByClassName("leaflet-overlay-pane")[0].children;
    for (var i = 0; i < mapLayers.length; i++) {
        if (mapLayers[i].innerHTML.includes(districtName)) {
            mapLayers[i].style.display = "block";
        }
    }
}
</script>
'''

folium_map.get_root().html.add_child(folium.Element(dropdown))

# Add layer controls
folium.LayerControl().add_to(folium_map)

# Save map
output_html = "D:/AgriMatrix/Area Calculation and Classification/sri_lanka_district_classified_map.html"
folium_map.save(output_html)
print(f"Map saved to {output_html}")


Map saved to D:/AgriMatrix/Area Calculation and Classification/sri_lanka_district_classified_map.html


In [6]:
folium_map